In [2]:
# Directories
import os
os.chdir(r"E:\academy\OneDrive - IIT Delhi\3. IIT DELHI\2. Research\JRF\1_PAPER\2_Analysis")
print(os.getcwd())


E:\academy\OneDrive - IIT Delhi\3. IIT DELHI\2. Research\JRF\1_PAPER\2_Analysis


In [3]:
#Array packages
import cartopy.crs as ccrs
import pandas as pd
import numpy as np
import xarray as xr
import netCDF4 as nc4

from scipy.stats import kendalltau
import pymannkendall as mk

#plots
import matplotlib.pyplot as plt
import rioxarray as rio
import geopandas as gpd
from shapely.geometry import mapping
import matplotlib.ticker as ticker
from matplotlib.ticker import MultipleLocator

#Progress meter
from dask.diagnostics import ProgressBar
from tqdm import tqdm

# Directories
import os
import glob
import dask
#import h5netcdf
import scipy


In [4]:
mdl=5
gdf_p=gpd.read_file('DATA_p/shapefile/south_asia_p.shp')
model=["LIS_MERRA2","LIS_IMD","LIS_CHIRPS","LIS_ERA5","LIS_IMDc","LIS_IMDcnew"]
var=['TotalPrecip_tavg','Evap_tavg','Qs_tavg','RE','RE_cleaned']

ds = xr.open_mfdataset(f'DATA_p/LIS/{model[mdl]}/{model[mdl]}_grid_All.nc',engine='netcdf4', parallel=True,chunks={'time': 'auto'})
#ds=ds.mean(dim='SoilMoist_profiles')

ds

<xarray.Dataset>
Dimensions:           (time: 504, lat: 320, lon: 300, SoilMoist_profiles: 4)
Coordinates:
  * time              (time) datetime64[ns] 1980-01-31 1980-02-29 ... 2021-12-31
    spatial_ref       int64 ...
  * lat               (lat) float64 5.55 5.65 5.75 5.85 ... 37.25 37.35 37.45
  * lon               (lon) float64 68.05 68.15 68.25 ... 97.75 97.85 97.95
Dimensions without coordinates: SoilMoist_profiles
Data variables: (12/20)
    Swnet_tavg        (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    Lwnet_tavg        (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    Qle_tavg          (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    Qh_tavg           (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    Qg_tavg           (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    Snowf_tavg        (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    ...                ...
    WaterTableD_tavg  (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    TWS_tavg          (time, lat, lon) float64 dask.array<chunksize=(168, 320, 300), meta=np.ndarray>
    GWS_tavg          (time, lat, lon) float64 dask.array<chunksize=(168, 320, 300), meta=np.ndarray>
    TotalPrecip_tavg  (time, lat, lon) float32 dask.array<chunksize=(252, 320, 300), meta=np.ndarray>
    RE                (time, lat, lon) float64 dask.array<chunksize=(168, 320, 300), meta=np.ndarray>
    RE_cleaned        (time, lat, lon) float64 dask.array<chunksize=(168, 320, 300), meta=np.ndarray>

<xarray.Dataset>
Dimensions:           (time: 504, region: 18)
Coordinates:
  * time              (time) datetime64[ns] 1980-01-31 1980-02-29 ... 2021-12-31
    spatial_ref       int32 ...
  * region            (region) object 'Indus' 'Ganga' ... 'EFMP' 'West Flowing'
Data variables:
    TotalPrecip_tavg  (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    Evap_tavg         (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    Qs_tavg           (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    Qsb_tavg          (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    SoilMoist_tavg    (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    RE                (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    RE_cleaned        (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>

In [25]:
ds_RM['SoilMoist_tavg']=ds_RM['SoilMoist_tavg'].rolling(time=2).mean()
ds_RM.isel(region=1)['SoilMoist_tavg'].compute()
ds_RM.isel(region=1)['RE_cleaned'].compute()

df=ds_RM.isel(region=1).compute().to_dataframe()
df

SoilMoist_tavg  RE_cleaned  TotalPrecip_tavg  spatial_ref region
time                                                                        
1980-01-31             NaN    0.014108          5.358762            0  Ganga
1980-02-29             NaN    0.011080          9.546745            0  Ganga
1980-03-31        0.254572    0.020562         18.250322            0  Ganga
1980-04-30        0.247372    0.031279          7.950562            0  Ganga
1980-05-31        0.239872    0.019371         45.378513            0  Ganga
...                    ...         ...               ...          ...    ...
2021-08-31        0.312959    0.077865        292.933105            0  Ganga
2021-09-30        0.340299    0.044571        185.713593            0  Ganga
2021-10-31        0.346205    0.053205        113.433456            0  Ganga
2021-11-30        0.330002    0.007661          4.290324            0  Ganga
2021-12-31        0.308094    0.009520         16.800058            0  Ganga

[504 rows x 5 columns]

## PLOT_AMC RE plot

In [7]:
lsm

<xarray.Dataset>
Dimensions:           (region: 18, time: 504)
Coordinates:
  * time              (time) datetime64[ns] 1980-01-31 1980-02-29 ... 2021-12-31
    spatial_ref       int32 ...
  * region            (region) object 'Indus' 'Ganga' ... 'EFMP' 'West Flowing'
Data variables:
    SoilMoist_tavg    (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    RE_cleaned        (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>
    TotalPrecip_tavg  (region, time) float64 dask.array<chunksize=(18, 504), meta=np.ndarray>

In [12]:
import matplotlib.ticker as ticker
import matplotlib.font_manager as fm
import matplotlib.patches as mpatches  # Import mpatches for creating legend patches
from matplotlib.lines import Line2D
import scienceplots

plt.style.use(['science','no-latex'])

mdl=5
model=["LIS_MERRA2","LIS_IMD","LIS_CHIRPS","LIS_ERA5","LIS_IMDc","LIS_IMDcnew"]
lsm = xr.open_mfdataset(f'DATA_p/LIS/{model[mdl]}/{model[mdl]}_reg_All.nc',engine='netcdf4', parallel=True,chunks={'time': 'auto'})
basin=lsm.region.values


fig, ax = plt.subplots(5,4,figsize=(17,13), facecolor='white', dpi=600,sharey=True)
ax=ax.flatten()


var=['TotalPrecip_tavg','Evap_tavg','Qs_tavg','RE','RE_cleaned','SoilMoist_tavg']
var1=['PPT','ET','Qs','RE','RE_clean','Soil moisutre']
ssn=['Pre-monsoon','Monsoon','Post-monsoon','Winter']
amc_lab=['AMC1','AMC2','AMC3']
ssn_m=[[3,4,5],[6,7,8,9],[10,11],[12,1,2]]
col=['indianred','darkslateblue','mediumseagreen','grey']
marker=['o','s','v']

lsm=lsm[['SoilMoist_tavg','RE_cleaned','TotalPrecip_tavg']]
lsm['SoilMoist_tavg']=lsm['SoilMoist_tavg']/(60*24*60)
lsm['SoilMoist_tavg']=lsm['SoilMoist_tavg'].rolling(time=2).mean()      # to consider antecedent effect or shift the timeseries


for i in range(18):
        
    
    lsm1=lsm.isel(region=i,time=np.arange(3,504,2)) # reducing points so it would be visible
   
    df=lsm1.compute().to_dataframe()

    for j in range(4):
        df.loc[df.index[df.index.month.isin(ssn_m[j])],'color']=col[j] 

    ppt=df['TotalPrecip_tavg']
    sm=df['SoilMoist_tavg']
    re=df['RE_cleaned']    
    
    p_30 = np.percentile(sm, 30);p_60 = np.percentile(sm, 60)
    amc = np.where(sm < p_30, 'AMC1',np.where((sm >= p_30) & (sm < p_60), 'AMC2', 'AMC3'))
    marker_dic = dict(zip(np.unique(amc),marker))

    [x.set_linewidth(1.25) for x in ax[i].spines.values()]
    ax[i].grid(True, color= 'grey', alpha=0.4, linestyle='dotted')
 
        # Plotting based on AMC shape and season color (Note that AMC doesnt accept series of shapes)
    for amc_type in np.unique(amc):
        ax[i].scatter(
            ppt[amc == amc_type], re[amc == amc_type],
            c=df['color'][amc == amc_type],  # Seasonal color
            marker=marker_dic[amc_type],    # AMC shape
            alpha=1, s=25
        )

    ax[i].set_xlim(0,np.quantile(ppt,0.95))
    ax[i].set_ylim(0,0.18)


    ax[i].xaxis.set_tick_params(which='both', bottom=True, top=False,labelsize=21.5) 
    ax[i].yaxis.set_tick_params(which='both', left=True, right=False,labelsize=21.5) 
    
    #ax[i].text(0.73, 0.97,f"R2 : {np.corrcoef(ppt,re)[0,1].round(2)} ", fontsize=19.5, color='darkblue',ha='left', va='top', transform=ax[i].transAxes)
    
    
    #ax[i].set_title(f'{basin[i]}', fontsize=16.5,weight='bold',fontweight='bold')
    ax[i].text(0.05, 0.97, f'{basin[i]}', fontsize=20, weight='bold', ha='left', va='top', transform=ax[i].transAxes)
    
    lgnd=ax[i].legend(loc='center', ncol=2,fontsize=15, bbox_to_anchor=(0.2, 0.90),frameon=True, borderpad=0.2, edgecolor='black')
    frame = lgnd.get_frame()
    frame.set_linewidth(0.5)



    shd_per=[lsm['TotalPrecip_tavg'].isel(region=i).quantile(p).values for p in [.1,.5,.75]]
    
    ax[i].axvline(shd_per[0], color='grey', linestyle='--')
    ax[i].axvline(shd_per[1], color='grey', linestyle='--')
    ax[i].axvline(shd_per[2], color='grey', linestyle='--')
  
    # Create a secondary x-axis
    ax2 = ax[i].twiny()
    
    # Set ticks and labels for the secondary x-axis
    ax2.set_xlim(ax[i].get_xlim())
    ax2.set_xticks(shd_per)
    ax2.set_xticklabels([.25,.5,.75],fontsize=16)


# Season legend
legend_handles = [mpatches.Circle((0, 0), radius=5,color=col[i], label=ssn[i]) for i in range(4)]
legend_labels = ssn
fig.legend(handles=legend_handles, labels=legend_labels, loc='upper right', bbox_to_anchor=(0.68, 0.18), fontsize=19)


# AMC legend
# AMC legend handles and labels using Line2D for custom markers
legend_handles_amc = [Line2D([0], [0], marker=marker[i], color='black', markersize=10, linestyle='None', label=amc_lab[i]) for i in range(3)]
legend_labels_amc = amc_lab
fig.legend(handles=legend_handles_amc, labels=legend_labels_amc, loc='upper right', bbox_to_anchor=(0.8, 0.18), fontsize=19)


# Common xlabel and ylab
#plt.style.use('default')
fig.text(0.5, -0.02, 'Precipitation (mm/month)', ha='center', fontsize=26,fontweight='bold')
fig.text(-0.02, 0.5, 'Runoff Efficiency', va='center', rotation='vertical', fontsize=26, fontweight='bold')
#fig.suptitle(f'PPT vs Q ({model[mdl]})', fontsize=16,fontweight='bold',y=1)

[ax[i].axis('off') for i in range(18, 20)]
plt.tight_layout()

plt.savefig(f'7_Revision Analysis/mc1.png',dpi=300)
plt.show()

No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that artists whose label start with an underscore are ignored when legend() is called with no argument.
No artists with labels found to put in legend.  Note that 

96.04549789428711

In [ ]:
df=pd.DataFrame(index=basin,columns=['Variance AMC','Mean AMC','Min AMC','Max AMC','AMC_RE','AMC_RE_Monsoon','AMC_RE_PRE-Monsoon'])

for reg in basin:
    
    sm_reg=sm.sel(region=reg)
    ppt_reg=ppt.sel(region=reg)
    re_reg=re.sel(region=reg)

    df['Variance AMC'][reg]=np.var(sm_reg.values)/np.mean(sm_reg.values)
    df['Mean AMC'][reg]=np.mean(sm_reg.values)
    df['Min AMC'][reg]=np.min(sm_reg.values)
    df['Max AMC'][reg]=np.max(sm_reg.values)
    df['AMC_RE'][reg]=np.corrcoef(sm_reg.values,re_reg.values)[0,1]
    df['AMC_RE_Monsoon'][reg]=np.corrcoef(sm_reg.sel(time=sm['time.month'].isin([6,7,8])).values,re_reg.sel(time=sm['time.month'].isin([6,7,8])).values)[0,1]
    df['AMC_RE_PRE-Monsoon'][reg]=np.corrcoef(sm_reg.sel(time=sm['time.month'].isin([2,3,4])).values,re_reg.sel(time=sm['time.month'].isin([2,3,4])).values)[0,1]
    #df['AMC_RE_premonsoon'][reg]=np.corrcoef(sm_reg,re_reg)[0,1]

